In [70]:
import pandas as pd
import math
import os.path
import time
import numpy as np
import talib
from talib import abstract
from binance.client import Client
from datetime import timedelta, datetime
from dateutil import parser
#backtest lib
from backtesting import Backtest
from backtesting.lib import SignalStrategy
from backtesting.lib import crossover

In [71]:
### API
binance_api_key = 'TESZdWxapwvZG90v1SJ3zMahcXySUkYv3bxRRKXKkfCMANtUS0Dw38iWALACQuHU'    #Enter your own API-key here
binance_api_secret = 'Uw1V3mbqoXDm9II7tC8lHRrYcGslHKhqo2bEXGelt08bnAn5lk4EbYfbKmHjWguY' #Enter your own API-secret here
### CONSTANTS ----add 15min
binsizes = {"1m": 1, "5m": 5,"15m":15, "1h": 60, "4h": 240, "1d": 1440}
batch_size = 750
# api instance
binance_client = Client(api_key=binance_api_key, api_secret=binance_api_secret)

In [72]:
### get data funcs
def minutes_of_new_data(symbol, kline_size, data, source):
    if len(data) > 0:  old = parser.parse(data["timestamp"].iloc[-1])
    elif source == "binance": old = datetime.strptime('1 Jan 2017', '%d %b %Y')
    elif source == "bitmex": old = bitmex_client.Trade.Trade_getBucketed(symbol=symbol, binSize=kline_size, count=1, reverse=False).result()[0][0]['timestamp']
    if source == "binance": new = pd.to_datetime(binance_client.get_klines(symbol=symbol, interval=kline_size)[-1][0], unit='ms')
    if source == "bitmex": new = bitmex_client.Trade.Trade_getBucketed(symbol=symbol, binSize=kline_size, count=1, reverse=True).result()[0][0]['timestamp']
    return old, new

def get_all_binance(symbol, kline_size, save = False):
    filename = '%s-%s-data.csv' % (symbol, kline_size)
    # jsaw edit: not to get data from API if aiready exist data
    if os.path.isfile(filename): 
        print("read exist")
        data_df = pd.read_csv(filename)
        return data_df
    else: 
        data_df = pd.DataFrame()
    oldest_point, newest_point = minutes_of_new_data(symbol, kline_size, data_df, source = "binance")
    delta_min = (newest_point - oldest_point).total_seconds()/60
    available_data = math.ceil(delta_min/binsizes[kline_size])
    if oldest_point == datetime.strptime('1 Jan 2017', '%d %b %Y'): 
        print('Downloading all available %s data for %s. Be patient..!' % (kline_size, symbol))
    else: 
        print('Downloading %d minutes of new data available for %s, i.e. %d instances of %s data.' % (delta_min, symbol, available_data, kline_size))
    klines = binance_client.get_historical_klines(symbol, kline_size, oldest_point.strftime("%d %b %Y %H:%M:%S"), newest_point.strftime("%d %b %Y %H:%M:%S"))
    data = pd.DataFrame(klines, columns = ['timestamp', 'open', 'high', 'low', 'close', 'volume', 'close_time', 'quote_av', 'trades', 'tb_base_av', 'tb_quote_av', 'ignore' ])
    data['timestamp'] = pd.to_datetime(data['timestamp'], unit='ms')
    if len(data_df) > 0:
        temp_df = pd.DataFrame(data)
        data_df = data_df.append(temp_df)
    else: 
        data_df = data
    data_df.set_index('timestamp', inplace=True)
    data_df = data.astype(float)
    if save: 
        data_df.to_csv(filename)
    print('All caught up..!')
    return data_df

In [154]:
#get data since 2017.7.1

df_4hr = get_all_binance('BTCUSDT', '4h',True)
df_1hr = get_all_binance('BTCUSDT', '1h',True)
df_15min = get_all_binance('BTCUSDT', '15m',True)
df_5min = get_all_binance('BTCUSDT', '5m', True)
df_1min = get_all_binance('BTCUSDT', '1m',True)

read exist
read exist
read exist
read exist
read exist


In [158]:
df = df_15min
df

timestamp      open      high       low     close  \
0      2019-11-01 00:00:00   9140.86   9144.70   9106.81   9128.33   
1      2019-11-01 00:15:00   9129.05   9129.05   9098.28   9108.63   
2      2019-11-01 00:30:00   9108.65   9126.08   9101.00   9107.91   
3      2019-11-01 00:45:00   9107.46   9127.82   9104.13   9125.52   
4      2019-11-01 01:00:00   9127.00   9141.70   9120.96   9133.00   
...                    ...       ...       ...       ...       ...   
36255  2020-11-13 10:45:00  16192.64  16249.20  16165.00  16201.14   
36256  2020-11-13 11:00:00  16201.58  16217.36  16085.00  16142.76   
36257  2020-11-13 11:15:00  16142.79  16202.56  16070.17  16164.31   
36258  2020-11-13 11:30:00  16164.31  16207.51  16164.30  16197.36   
36259  2020-11-13 11:45:00  16197.35  16240.82  16181.38  16225.00   

            volume    close_time      quote_av   trades  tb_base_av  \
0       426.576392  1.572567e+12  3.893280e+06   3804.0  225.314734   
1       371.226445  1.572568e+12  3.382230e+06   3985.0  190.286949   
2       310.988756  1.572569e+12  2.834068e+06   4597.0  159.760082   
3       203.266533  1.572570e+12  1.853247e+06   3719.0  119.620348   
4       172.847246  1.572571e+12  1.578487e+06   4080.0   96.323358   
...            ...           ...           ...      ...         ...   
36255  1136.470529  1.605265e+12  1.842120e+07  14359.0  531.188814   
36256  1965.495613  1.605266e+12  3.172010e+07  23569.0  761.895751   
36257  1183.000678  1.605267e+12  1.907143e+07  17901.0  554.062217   
36258   818.015813  1.605268e+12  1.324403e+07  11248.0  343.370616   
36259   950.379914  1.605269e+12  1.541508e+07  12280.0  303.094020   

        tb_quote_av  ignore  
0      2.056464e+06     0.0  
1      1.733707e+06     0.0  
2      1.455884e+06     0.0  
3      1.090669e+06     0.0  
4      8.796145e+05     0.0  
...             ...     ...  
36255  8.610680e+06     0.0  
36256  1.229849e+07     0.0  
36257  8.934188e+06     0.0  
36258  5.559089e+06     0.0  
36259  4.916134e+06     0.0  

[36260 rows x 12 columns]

In [188]:
class StrategyMACD(SignalStrategy):
    #optimize parameter
    
    #15min 24,20
    RSIperiod = 24
    RSICloseUpTrigger = 70
    RSICloseDownTrigger = 20
    RSIOpenTrigger = 50
    
    
    def init(self):
        super().init()
        
        #get strategy data
        df = self.getDf()
        #EMA
        df['EMA5'] = talib.EMA(df['close'], timeperiod=5)
        df['EMA10'] = talib.EMA(df['close'], timeperiod=10)
        df['EMA20'] = talib.EMA(df['close'], timeperiod=20)
        df['EMA60'] = talib.EMA(df['close'], timeperiod=60)
        df['EMA200'] = talib.EMA(df['close'], timeperiod=200)
        #MACD
        macdFast, macdSlow, histogram = talib.MACD(df['close'].values, fastperiod=12, slowperiod=26, signalperiod=9)
        df['MACD_DIF'] = macdFast
        df['MACD_DIM'] = macdSlow
        df['MACD_HIS'] = histogram
        #RSI
        df['RSI'] = talib.RSI(df['close'], timeperiod=self.RSIperiod)
        #print(df['RSI'])
        # cache to class for signal
        self.high = df['high']
        self.low = df['low']
        self.open = df['open']
        self.close = df['close']
        df['preClose'] = df['close'].shift(periods=1)

        signal_long = (self.close > df['EMA5']) & (df['EMA5'] > df['EMA10']) & (df['EMA10'] > df['EMA20']) & (df['EMA20'] > df['EMA60'])\
        & (df['EMA60'] > df['EMA200']) & (df['preClose'] < df['EMA5']) & (df["MACD_DIF"] > df["MACD_DIM"]) 
        #print(signal_long)
        
        signal_closePosition = (self.close < df['EMA5']) &  (df["RSI"] < self.RSICloseDownTrigger)
        #signal = signal_long
        #signal[signal_short] = -1
        self.set_signal(signal_long, signal_closePosition)
        
    def getDf(self):
        df = pd.DataFrame(columns=['open','high', 'low', 'close','volume'])
        df['open'] = pd.Series(self.data.Open)
        df['close'] = pd.Series(self.data.Close)
        df['high'] = pd.Series(self.data.High)
        df['low'] = pd.Series(self.data.Low)
        return df
        
    def next(self):
        #if(self.position.pl_pct > 0.3):
        #   self.position.close()
        #if(self.position.pl_pct < -0.05):
        #    self.position.close()
            
        super().next()

In [189]:
backtestData = df.rename(columns={"open": "Open", "high": "High", "low": "Low", "close": "Close","volume":"Volume"})
backtestData = backtestData[["Open","High","Low","Close","Volume"]]
result1 = Backtest(backtestData, StrategyMACD, cash=100000, commission=.002)
print(result1.run())
result1.plot()

<ipython-input-189-005da5f7c270>:3: UserWarning: Data index is not datetime. Assuming simple periods, but `pd.DateTimeIndex` is advised.
  result1 = Backtest(backtestData, StrategyMACD, cash=100000, commission=.002)


Start                                       0
End                                     36259
Duration                                36259
Exposure Time [%]                     69.4374
Equity Final [$]                       315099
Equity Peak [$]                        319634
Return [%]                            215.099
Buy & Hold Return [%]                 77.7434
Max. Drawdown [%]                    -23.6115
Avg. Drawdown [%]                    -1.77935
Max. Drawdown Duration                   8213
Avg. Drawdown Duration                 192.52
# Trades                                   89
Win Rate [%]                          76.4045
Best Trade [%]                        58.9734
Worst Trade [%]                      -7.74251
Avg. Trade [%]                        16.5067
Max. Trade Duration                      9901
Avg. Trade Duration                   4603.97
Profit Factor                         13.5431
Expectancy [%]                        21.5672
SQN                               

In [62]:
stats._strategy


<Strategy StrategyMACD(RSIperiod=12,RSICloseTrigger=72)>

In [61]:
#optimize
stats = result1.optimize(RSIperiod=range(5, 16, 1),
                         RSICloseTrigger=range(70, 95, 2),
                    maximize='Equity Final [$]')
stats

Start                                       0
End                                     36259
Duration                                36259
Exposure Time [%]                     46.6685
Equity Final [$]                       220554
Equity Peak [$]                        223657
Return [%]                            120.554
Buy & Hold Return [%]                 77.7434
Max. Drawdown [%]                    -17.3144
Avg. Drawdown [%]                     -1.6104
Max. Drawdown Duration                   5323
Avg. Drawdown Duration                184.661
# Trades                                   95
Win Rate [%]                          69.4737
Best Trade [%]                        30.3344
Worst Trade [%]                       -13.752
Avg. Trade [%]                        6.89922
Max. Trade Duration                      5253
Avg. Trade Duration                   2300.09
Profit Factor                         5.78792
Expectancy [%]                        10.7181
SQN                               